In [1]:
!apt install -q ffmpeg
!pip install -q ffpb

Reading package lists...
Building dependency tree...
Reading state information...
ffmpeg is already the newest version (7:4.4.2-0ubuntu0.22.04.1).
0 upgraded, 0 newly installed, 0 to remove and 45 not upgraded.


In [11]:
from google.colab import files
_ = files.upload()

Saving NotoSerifMalayalam-VariableFont_wght.ttf to NotoSerifMalayalam-VariableFont_wght.ttf


In [ ]:
!ffpb -i '/content/Intro to Large Language ModelsEP001_ml.mp4' -vf subtitles='/content/LLM_ml.srt'

# For the translated subtitle in another language, you may need to get corresponding font in order for it to be displayed correctly in video.
# !ffpb -i $video -vf subtitles=$sub_translated -y $subtitled

/content/Intro to Large Language ModelsEP001_ml.mp4: Invalid data found when processing input


In [ ]:
# prompt: using ffpb library add  translated subtitle in another language,  get corresponding font in order for it to be displayed correctly in video.

#!apt install fonts-wqy-zenhei
#!ffpb -i $video -vf subtitles=$sub_translated -c:v libx264 -crf 23 -c:a aac -b:a 128k -vf "ass=sub_translated.ass,format=yuv420p" $subtitled_translated


In [ ]:
!pip install moviepy==2.0.0.dev2
!pip install imageio==2.25.1

In [ ]:
!apt install imagemagick

In [5]:
!cat /etc/ImageMagick-6/policy.xml | sed 's/none/read,write/g'> /etc/ImageMagick-6/policy.xml

In [ ]:
!pip install pysrt==1.1.2

In [9]:
# Place files in this path or modify the paths to point to where the files are
srtfilename = "/content/captions.srt"
mp4filename = "/content/LLMEP001_ml.mp4"

In [12]:
!cp /content/NotoSerifMalayalam-VariableFont_wght.ttf /usr/share/fonts/truetype/

In [21]:
!ls -l /usr/share/fonts/truetype/NotoSerifMalayalam-VariableFont_wght*

-rw-r--r-- 1 root root 231336 Jun 14 05:42 /usr/share/fonts/truetype/NotoSerifMalayalam-VariableFont_wght.ttf


In [ ]:
# ref: https://thottingal.in/blog/2022/10/05/nupuram/
!wget https://smc.gitlab.io/fonts/Nupuram/fonts/Nupuram-Color.zip

In [ ]:
!unzip /content/Nupuram-Color.zip

In [35]:
import sys
import pysrt
from moviepy.editor import VideoFileClip, TextClip, CompositeVideoClip


def time_to_seconds(time_obj):
    return time_obj.hours * 3600 + time_obj.minutes * 60 + time_obj.seconds + time_obj.milliseconds / 1000


def create_subtitle_clips(subtitles, videosize,fontsize=24, font='/content/fonts/Nupuram-Color/otf-color/Nupuram-Color.colrv1.otf', color='yellow', debug = False):
    subtitle_clips = []

    for subtitle in subtitles:
        start_time = time_to_seconds(subtitle.start)
        end_time = time_to_seconds(subtitle.end)
        duration = end_time - start_time

        video_width, video_height = videosize

        text_clip = TextClip(subtitle.text, fontsize=fontsize, font=font, color=color, bg_color = 'black',size=(video_width*3/4, None), method='caption').set_start(start_time).set_duration(duration)
        subtitle_x_position = 'center'
        subtitle_y_position = video_height* 4 / 5

        text_position = (subtitle_x_position, subtitle_y_position)
        subtitle_clips.append(text_clip.set_position(text_position))

    return subtitle_clips

In [10]:
# Load video and SRT file
video = VideoFileClip(mp4filename)
subtitles = pysrt.open(srtfilename)

begin,end= mp4filename.split(".mp4")
output_video_file = begin+'_subtitled'+".mp4"

print ("Output file name: ",output_video_file)

Output file name:  /content/LLMEP001_ml_subtitled.mp4


In [36]:
# Create subtitle clips
subtitle_clips = create_subtitle_clips(subtitles,video.size)

# Add subtitles to the video
final_video = CompositeVideoClip([video] + subtitle_clips)

# Write output video file
final_video.write_videofile(output_video_file)


Moviepy - Building video /content/LLMEP001_ml_subtitled.mp4.
MoviePy - Writing audio in LLMEP001_ml_subtitledTEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video /content/LLMEP001_ml_subtitled.mp4



t:  99%|█████████▉| 4824/4884 [02:53<00:01, 33.08it/s, now=None]/usr/local/lib/python3.10/dist-packages/moviepy/video/io/ffmpeg_reader.py:154: UserWarning: In file /content/LLMEP001_ml.mp4, 2764800 bytes wanted but 0 bytes read,at frame index 4826 (out of a total 4826 frames), at time 160.87/160.89 sec. Using the last valid frame instead.
  warnings.warn(


Moviepy - Done !
Moviepy - video ready /content/LLMEP001_ml_subtitled.mp4


In [38]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open(output_video_file,'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=600 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)